## BASH Scripting

First - I only will cover BASH (Bourne Again SHell) scripting here. However, all of the scripts, written in BASH, will also be available for (T)CSH (C-SHell), and you can compare them with the BASH material here to see how you can do the same in (T)CSH.

That said, BASH is much more common in practice, better to debug, and in general safer. Also, [this](http://www.shlomifish.org/open-source/anti/csh/) site outlines several specific reasons to avoid TCSH.

Here I will introduce the essentials.

As an aside: Here are some **resources** that I look at often:

[Here](http://www.grymoire.com/Unix/Quote.html) for how to do quoting for variables depending on if its in a script, or in a sed command etc.

[Here](http://tldp.org/LDP/abs/html/comparison-ops.html) for how to do if/else testing.

### Variables

Variables are created by assignment: `A=B` would assign to variable *A* the value "B". Note that no spaces exists. This is key. In fact, I'll repeat it: **VARIABLE ASSIGNMENTS *REQUIRE* NO SPACES**. 

You can also assign variables with the `export` command, which does the same as above, but also means all child processes from the current shell will *also* be aware of this variable. 

Variables are accessed with the `$` symbol. While `$VARIABLENAME` is sufficient, sometimes you want to use it next to other letters, which can confuse the shell parser. For example, say you want to make a directory called "ENTERED_NAME"DIR, then how would the parser know when the variable name ends and the string begins? This is done by using the `{}` symbols.

##### Multiple commands on a single line: 
This can be done by connecting them with the ";" symbol, similar to *C*.

In [ ]:
VAR=Bananas
echo $VAR
mkdir $VARDir # Should return an error message
mkdir ${VAR}Dir
ls
VAR2=Apples ; echo $VAR2 ; echo "I like Granny Smiths" > $VAR2 ; ls
VAR3=${VAR}${VAR2} ; echo VAR3=$VAR3
VAR3="${VAR}${VAR2}" ; echo VAR3=$VAR3
VAR3='${VAR}${VAR2}' ; echo VAR3=$VAR3

#### The `let` operator
`let` is a convenient way of telling BASH that the variable isn't a string, but instead is an integer. It then will evaluate +-\*/ signs appropriately. These variables are still referenced with the `$` symbol. **Again, no spaces can appear**

In [ ]:
let VAR4=5 ; echo $VAR4
let VAR5=3+${VAR4} ; echo $VAR5
let VAR5=3*${VAR4} ; echo $VAR5
let VAR5=3/${VAR4} ; echo $VAR5
let VAR5=7/${VAR4} ; echo $VAR5
let $VAR4=$VAR4+1 ; echo $VAR4

Unfortunately, BASH doesn't have a straight-forward float manipulator. But if you need to do float arithmetic, you should probably be using a more typical programming language, like C,C++,F95,python, etc.

#### The \`...\` operator
The "\`...\`" operator means evaluate what is inside, then convert it to a string as if it was given as input

Need to get another file:

In [ ]:
wget https://bitbucket.org/mlarichardson/introduction-to-unix/raw/953ea44e6ec21ee393611c4dc93db611666ea658/NewFiles_2015_11_01.tgz

Or click [here](https://bitbucket.org/mlarichardson/introduction-to-unix/raw/953ea44e6ec21ee393611c4dc93db611666ea658/NewFiles_2015_11_01.tgz).

In [ ]:
let NUMLINES=`wc -l Prof_R_Rho_Wide_7.txt | awk '{print $1}'` ; echo $NUMLINES

#### Lists vs Arrays
You can make a list of files that are relevant for a task with "..." where "..." would make `ls` return those filenames. For example:

In [ ]:
ls Prof_*
files="Prof_*"
echo $files

**WARNING** - the variable "files" DOES NOT equal the list of files. It actually equals the "...", but BASH knows that when you call on the value to use the files in the same directory that match it. See:

In [ ]:
cd ../
echo $files

This is crucial! And definitely a mistake I've made before. If you want to make an array variable that has the list of files, you can do that with the `()` operators:

In [ ]:
cd Files_2015_11_01
files=(Prof_*)
echo ${files[*]}
echo $files
echo ${files[0]}
echo ${files[1]}
cd ../
echo ${files[1]}
cd Files_2015_11_01

Alright, now for the two most important bits of BASH scripting (ASIDE: wait, are we actually ever going to write a script? We have been! All of these sequences of commands are scripts, and they are what's most important. That said, we can put these in a file to make them reuseable ... almost there!)

#### `for` loops (similar to python)
For both the short-cut lists and arrays above, you can do very simple for loops! Just be sure if you do the former that it will expand properly (ie, you are in the correct directory!).

The syntax is (note! Indenting means nothing to the BASH parser):

In [ ]:
for IVAR in $LISTVAR
do
  COMMAND 1
  COMMAND 2
done

Although I prefer:

In [ ]:
for IVAR in $LISTVAR ; do
  COMMAND 1
  COMMAND 2
done

Or on a single line:

In [ ]:
for IVAR in $LISTVAR ; do COMMAND 1 ; COMMAND 2 ; done

In [ ]:
# Here's an example
files=(Prof_*)
echo ${files[*]}
for f in ${files[*]} ; do
  wc -l $f
  head -2 $f
done

echo " "

files="Prof_*"
echo $files
for f in $files ; do
  wc -l $f
  head -2 $f
done

#### `if`/`elif`/`else`

The syntax is very similar to the `for` structure.

In [ ]:
if [[ TEST ]] ; then
  COMMAND 1
  COMMAND 2
elif [[ NEWTEST ]] ; then
  COMMAND 3
  COMMAND 4
else
  COMMAND 3
  COMMAND 4
fi

Important notes:
- I exclusively use the double square brackets. This impacts the types of conditionals you can check, and the syntax, but it has the most power.
- The double square brackets must be preceeded and followed by a space, as must all individual values inside. 
- If your "TEST" is a comparison it matters whether you are doing integer comparison or string comparison:
    - Comparing strings: Use "..." to mean exactly inside.  
    - Comparisons are:
        - = : are the same
        - == : are the same, although the second argument can be a regular expressions and the result is true if the regular expression would return that value.
        - != : are not the same
        - < : less than in ascii character order
        - \> : greater than in ascii character order
        - -z : empty string
        - -n : non-empty string
        - -e : checks if the string exists as a file
    - Comparing integers: no quotes are used here.
    - Comparisons are very similar to old Fortran77:
        - -eq : equal
        - -ne : not equal
        - -gt : greater than
        - -ge : greater than or equal
        - -le : less than or equal
        - -lt : less than
- You can use && and || for AND and OR
- ! is a negate sign, which flips the value inside the brackets (TRUE to FALSE) 
- Note: only the empty string really returns as False. (`var=`"")

To speed things along, I thought it would be best to learn the `if` synatax via examples in a BASH script, so first here's what you need to know for a BASH script file.

In [ ]:
#!/bin/bash

VAL="CHEESE"
if [[ $VAL == WHEY ]] ; then
  echo "You eat that Whey"
elif [[ $VAL == MILK ]] ; then
  echo "You drink that Milk"
elif [[ -z $VAL ]] ; then
  echo "I guess there's nothing. :( "
else
  echo "Enjoy your " $VAL
fi

let VAL=13
ls
if [[ $VAL -lt 10 ]] ; then
  touch new_file_000$VAL
elif [[ $VAL -lt 100 ]] ; then
  touch new_file_00$VAL
elif [[ $VAL -lt 1000 ]] ; then
  touch new_file_0$VAL
else
  touch new_file_00$VAL
fi
ls

if [[ $VAL -gt 10 ]] ; then echo "It's greater than 10 so use numerals instead of letters." ; fi

**While** loops:

You can loop until a condition is met with the `while` loop:

`while [[ CONDITION ]] ; do`

    COMMANDS

`done`

In [ ]:
files="Prof_R_*"
for f in $files ; do
  if [[ $f == "Prof_R_T_Wide_7.txt" ]] ; then
    echo $f
    echo "done"
    break
  else
    continue
  fi
  echo "here"
done

You can skip to the next iteration of the loop with the `continue` command, while you can break out of the the loop with the `break` command.

### Writing a BASH Script file
To begin, I usually start off by nameing scripts with the suffix ".sh" until they are ready to use freely.

The first line should be "#!/bin/bash"

"#" Is used at the beginning of a line to indicate a comment. Like for parallel code, the #! tells the parser that it's a special instruction. Here you are saying this script is written for the bash shell.

To exit out of a script in the middle you can use the `exit` command, and you can return a value, typically 1 for an error.

There are some special variables that are passed to the script:

** $# is the Number of arguments **

** $1 is the first argument **

** $2 is the second argument ** etc.

If `$N` has `N > $#`, then it will return an empty string. 

Once the script does what you want, you can make it executable by typing:
`chmod +x SCRIPT.sh`. It's usually at this point that I remove the ".sh" suffix and move the script
to a directory in my PATH (usually ~/bin/).

And now you're good to go! Let's look quickly at two scripts that should be in your new directory: RoleCall and MakeSAve.sh

In [ ]:
./RoleCall Test
./RoleCall R
cat RoleCall

cat MakeSAve.sh
./MakeSAve.sh # This will raise an error that you don't have permission

ls -l MakeSAve.sh

bash MakeSAve.sh
chmod +x MakeSAve.sh
mv MakeSAve.sh MakeSAve
./MakeSAve

ls Prof_*
./MakeSAve 7
ls Prof_*

Some last useful things: Bang!

- `!$` : The last argument past to the previous command
- `!a` : The last command you entered that started with a 
- `!!` : the last command you entered (Bang Bang!)